# Практическая работа №8 "Задача коммивояжера"
Разработать алгоритм решения задачи коммивояжера.
### Импорт необходимых библиотек

In [70]:
import folium
import pandas as pd
import numpy as np

from csv import DictWriter
from math import sqrt

from algorythm import aco

### Считывание данных

In [80]:
df = pd.read_csv('data.csv', delimiter=',', index_col='id')

In [81]:
df

region        municipality   settlement type  \
id                                                                  
0          Республика Алтай   Шебалинский район        Каспа    с   
1            Алтайский край          Смоленский     Молочный    п   
2         Красноярский край   Казачинский район      Отношка    с   
3           Республика Тыва  Каа-Хемский кожуун    Кундустуг    с   
4         Красноярский край   Курагинский район    Щетинкино    с   
...                     ...                 ...          ...  ...   
6132  Новосибирская область     Сузунский район       Мереть    с   
6133  Новосибирская область     Сузунский район      Маюрово    с   
6134         Алтайский край     Быстроистокский   Смоленский    п   
6135  Новосибирская область   Искитимский район    Малиновка    д   
6136      Красноярский край   Назаровский район  Старожилово    п   

      latitude_dd  longitude_dd  
id                               
0            5111          8601  
1            5241          8497  
2            5738          9270  
3            5157          9518  
4            5453          9344  
...           ...           ...  
6132         5357          8239  
6133         5431          8242  
6134         5221          8466  
6135         5466          8386  
6136         5583          9088  

[6137 rows x 6 columns]

latitude_dd и longitude_dd это целые числа полученные путем умножения исходного значения на 100 и последующего округления до ближайшего целого. Для преобразования в исходное значение (например, для нанесения на карту) достаточно поделить на 100.

In [82]:
df[["latitude_dd", "longitude_dd"]] = df[["latitude_dd", "longitude_dd"]].apply(lambda x: x / 100)

### Отображение карты с точками населённых пунктов

In [83]:
country_map = folium.Map(
    location=[64.0914, 101.6016],  # Широта и долгота России
    tiles='Stamen Toner',  # Высококонтрастные черно-белые карты.
    zoom_start=4  # Начальный уровень масштабирования
)

In [84]:
for _, row in df.iterrows():
    folium.Circle(
        radius=5,
        location=(row['latitude_dd'], row['longitude_dd']),
        popup=row['settlement'],
        color='crimson',
        fill=True,
    ).add_to(country_map)

country_map

Определим функцию для рассчёта расстояния между населенными пунктами как евклидово расстояние между точками.

In [85]:
def euclidean_distance(first_point: tuple, second_point: tuple) -> float:
    """
    Функция нахождения евклидового расстояния между двумя точками.
    :param first_point: Координаты первой точки
    :param second_point: Координаты второй точки
    :return: Евклидово расстояние
    """
    return sqrt((first[0] - second[0]) ** 2 + (first[1] - second[1]) ** 2)

Преобразуем объект DataFrame в numpy.ndarray

In [ ]:
df = df.to_numpy()

### Создание матрицы весов для муравьиного алгоритма
Матрица весов - это матрица, в которой каждый элемент представляет собой вес связи между двумя узлами графа. Матрица весов нужна для того, чтобы вычислять длину (или стоимость) маршрута, который строит муравей, и для того, чтобы обновлять количество феромона на ребрах графа в соответствии с правилом.

In [77]:
num = df.shape[0] # Количество строк в датафрейме

# Создаём квадратную матрицу и заполняем её нулями.
weight_matrix = np.zeros((num, num))
for first_index in range(num):
    for second_index in range(num):
        weight_matrix[first_index, second_index] = euclidean_distance(df[first_index, [4, 5]], df[second_index, [4, 5]])

### Решение задачи коммивояжера с помощью ACO (Ant Colony Optimization)
Алгоритм ACO (Ant Colony Optimization) - это способ оптимизации на основе популяции, который применяется для решения различных задач комбинаторной оптимизации, в том числе задачи коммивояжера. Основная идея алгоритма - моделирование поведения муравьев при поиске пищи. Муравьи обмениваются информацией о качестве найденных путей с помощью феромона, который они оставляют на тропе. Чем больше феромона на ребре графа, тем выше вероятность выбора этого ребра муравьем при построении маршрута. Таким образом, муравьи способны адаптироваться к изменяющимся условиям и находить оптимальные или приближенно оптимальные решения.

In [78]:
result_algo = aco(
    weight_matrix, 200, 200, ants=15, ages=160, rho=0.35,
    a=1, b=5, q=40, ph_min=0.001, ph_max=1000, elite=10
)

print(f"Длина маршрута: {result_algo[1]}")

Потраченное время: 133.34581040000012 секунд


458.64607843309756

In [79]:
with open("solution.csv", "w", encoding="utf-8") as csv:

    writer = DictWriter(
        csv, delimiter=";", lineterminator="\r",
        fieldnames=["Id", "Predicted"]
    )
    writer.writeheader()

    for i in range(len(result[0]) - 1):
        first, second = result[0][i], result[0][i + 1]

        writer.writerow({"Id": i, "Predicted": matrix[first, second]})